# Converter XML para dataframe Pandas

Importar as biblitecas necessárias

In [2]:
import pandas as pd
import requests
from xmltopd import extract_dataframe
import nltk

Função para inserção de categoria

In [22]:
def insert_category_and_tokenized_text(document: dict, category: str) -> dict:
    tokenized_text: list[str] = nltk.sent_tokenize(document.get("description", "No text"))
    
    document["description"] = "\n".join(tokenized_text)
    document["category"] = category
    
    return document

Fazer as requisições à API e destrinchar os XML.

In [23]:
news_categories: list[str] = [
    "brasil",
    "carros",
    "ciencia_e_saude",
    "concursos_e_emprego",
    "economia",
    "educacao",
    "loterias",
    "mundo",
    "musica",
    "natureza",
    "planeta-bizarro",
    "politica",
    "pop-arte",
    "tecnologia",
    "turismo-e-viagem"
]

news: list[dict] = []

for category in news_categories:
    news += [insert_category_and_tokenized_text(document=doc, category=category) for doc in extract_dataframe(
        requests.get("https://g1.globo.com/rss/g1/" + category + "/").text
    )]

news

[{'title': 'Batalha de Rap Macapá terá duelos de rima e venda de comidas típicas no Mercado Central',
  'link': 'https://g1.globo.com/ap/amapa/noticia/2023/05/05/batalha-de-rap-macapa-tera-duelos-de-rima-e-venda-de-comidas-tipicas-no-mercado-central.ghtml',
  'guid': 'https://g1.globo.com/ap/amapa/noticia/2023/05/05/batalha-de-rap-macapa-tera-duelos-de-rima-e-venda-de-comidas-tipicas-no-mercado-central.ghtml',
  'description': "   Evento ocorre neste sábado (6), a partir de 18h.\nInscrições são realizadas presencialmente das 8h às 14h na Secretaria Municipal de Direitos Humanos (Smdh).\nFinal da etapa estadual do Duelo de MC's, em Macapá\nLeandro Lennon/PMM\nO Mercado Central será o palco da Batalha de Rap Macapá neste sábado (6).\nO evento ocorre das 18h às 22h.\nAlém dos duelos de rima, haverá a venda de comidas típicas nos estandes de empreendedores locais.\nOs MC's interessados devem realizar a inscrição de maneira presencial, das 8h às 14h na Secretaria Municipal de Direitos Human

Criar um *dataframe* Pandas a partir dos dados

In [31]:
news_df: pd.DataFrame = pd.DataFrame(news)[["title", "description", "category"]].sample(frac=1)
news_df
    

title  \
1112  Cientista e engenheiro de dados estão em alta ...   
1105  Engenheira de dados desvenda desafios da área ...   
60    Polícia invade festa de facção criminosa no Ce...   
438   Resultado da Mega-Sena: 47 apostas da região a...   
338   Unicamp 2025: veja quando será o vestibular, d...   
...                                                 ...   
66    Prefeitura abre processo para contratação de e...   
237   Reforma tributária: imposto sobre herança ou d...   
37    Padre é atropelado por motorista embriagado pe...   
536   Eclipse solar na América do Norte leva multidã...   
850   Mulher é presa após latir para cão policial no...   

                                            description         category  
1112     Com desafio de encontrar mão de obra qualif...       tecnologia  
1105     Apesar de salários que podem passar de R$ 2...       tecnologia  
60        Com o grupo foram encontrados armas de fog...           brasil  
438      Já no sorteio da Lotofácil, apostadores de ...         loterias  
338      Comissão responsável pelo processo seletivo...         educacao  
...                                                 ...              ...  
66        Interessados devem entregar documentos de ...           brasil  
237      Texto da reforma prevê que imposto passe a ...         economia  
37        Teste do etilômetro apontou resultado três...           brasil  
536      Preços de hospedagem e passagens aéreas exp...            mundo  
850      Havia dois mandados de prisão contra ela, q...  planeta-bizarro  

[1300 rows x 3 columns]

Escrever *dataset* em **csv**

In [32]:
news_df.to_csv("g1.csv")

Escrever para arquivo

In [4]:
import os, sys

sys.path.append("../utils")

from convert_segformer import generate_segformer_docs

new_df: pd.DataFrame = pd.read_csv("g1.csv")


generate_segformer_docs(dataframe=new_df, folder="g1_news", text_body_field="description", max_doc_size=5, category_field="category")

[{'Unnamed: 0': 1112, 'title': 'Cientista e engenheiro de dados estão em alta e têm salário que pode passar de R$ 20 mil; veja como entrar', 'description': '   Com desafio de encontrar mão de obra qualificada, profissões seguem em alta em 2024 porque empresas valorizam cada vez mais o uso de dados na tomada de decisões.\nO g1 conversou com pessoas envolvidas nessas áreas para entender como está o mercado de trabalho.\nCientista e engenheiro de dados estão em alta e têm salário que pode passar de R$ 20 mil; veja como entrar\nArquivo pessoal\nNo universo da tecnologia da informação (TI), as áreas de cientista e engenheiro de dados são as atuais queridinhas do momento.\nElas oferecem salários realmente atrativos, mas encontram barreiras para procurar profissionais.\n➡️ Eis a explicação: elas são relativamente novas e fazem parte do boom da IA generativa.\nAs empresas estão atrás de quem realmente domina o assunto, mas são poucos aqueles que estão preparados.\nQuem já conseguiu se qualific